In [1]:
import sys 
import os

# Get the current working directory (the directory where the notebook is located)
notebook_dir = os.getcwd()

# Get the root directory by going up one level from the notebook directory
root_dir = os.path.abspath(os.path.join(notebook_dir, '..'))

# Add the root directory to the Python path, so this can stay nested
sys.path.append(root_dir)

In [2]:
# File name to run experiments on

# Different Test Cases
# timeStampFolder = "2024-10-17_11-48-23.791" # 5 UAVs hovering

# timeStampFolder = "2024-10-17_11-57-43.359" # Take-off (at least 4 drones)
# timeStampFolder = "2024-10-17_12-04-36.137" # Landing UAVs - for at least 2 UAVs
# timeStampFolder = "2024-10-17_15-59-35.092" # Up/Down Movement (for 5 UAVs)

# DJ Mini Tests - hovering overtop the radar tests, distances mentioned
# timeStampFolder = "2024-10-18_09-55-39.076 1.3m"
# timeStampFolder = "2024-10-18_09-59-12.941 5.0m"
# timeStampFolder = "2024-10-18_10-02-03.580 15m"
timeStampFolder = "2024-10-18_10-13-20.561 20m"
# timeStampFolder = "2024-10-18_10-10-43.904 29m"

In [3]:
import os
import time
import numpy as np
import pandas as pd
from scipy.fftpack import fft
from matplotlib import pyplot as plt

# Packages from the radar module
from radar.dataparsing.td_textdata_parser import read_columns
from radar.radarprocessing.RadarDataWindow import RadarDataWindow
from radar.configuration.CFARParams import CFARParams
from radar.configuration.RadarConfiguration import RadarConfiguration

# Setup the radar window 

radar_config = RadarConfiguration(config_path="/configuration/RadarConfig.yaml")
cfar_params = radar_config.cfar_params

# Optional overrides of those params
# cfar_params.num_guard = 5
# cfar_params.num_train = 15
# cfar_params.threshold = 2.5

start_time = pd.Timestamp.now()

# Setup the default Radar Window
radar_window = RadarDataWindow(cfar_params=cfar_params,
                                            start_time=start_time,
                                            capacity=200,
                                            run_velocity_measurements=False)

directory_to_process = f"/data/radar/Oct17/{timeStampFolder}/TD"

#### Add the plots we can populate with data

In [4]:
from plots.PlotFunctions import plot_polar_detections, plot_cartesian_detections, plot_xy_detections

## Plots that will be used -- Polar and Cartesian plots
fig_polar, ax_polar = plt.subplots(subplot_kw={'projection': 'polar'}, figsize=(6, 6))
fig_cartesian, ax_cartesian = plt.subplots(figsize=(6, 6))
fix_xy, ax_xy = plt.subplots(figsize=(6, 6))

fig_polar.suptitle("Radar Detections - Polar Plot")
fig_cartesian.suptitle("Radar Signal - Cartesian Plot")
fix_xy.suptitle("Radar Detections Location")

# Close the figures to prevent static images from being displayed statically (will be shown dynamically below)
plt.close(fig_polar)
plt.close(fig_cartesian)
plt.close(fix_xy)

### Add data to the radar window
The goal of this section is to simulate in a notebook, how the Radar Window is processing the incoming TDData. 

It should simulate the same behaviour and code used in the "radar_tracking.py" file, but is using the window directly, without using queues to pass the files along.

In [5]:
# Read the files
files = os.listdir(directory_to_process)

# Filter the files based on the naming convention
txt_files = [f for f in files if f.endswith('.txt')]

# Sort the files if needed (optional)
txt_files.sort()

In [ ]:
# List all files in the directory
from matplotlib.animation import FuncAnimation

# Process the data from the folder, adding it to the radar window 1 by 1
def update(frame):
    # Clear each figure's axes for the new frame
    ax_polar.clear()
    ax_cartesian.clear()
    ax_xy.clear()
    
    # If we haven't already processed the frame (i.e. in a previous run, add it)
    if len(radar_window.raw_records) <= frame:
        file_path = os.path.join(directory_to_process, txt_files[frame])
        new_td_data = read_columns(file_path)
        
        # print (f"Processing Frame: {frame}")
        radar_window.add_raw_record(new_td_data)
        radar_window.process_data()
        
    latest_td_data = radar_window.raw_records[-1]
    
    # Since we're doing CFAR on the 512 records there is always enough data to process
    detection_record = radar_window.detection_records[frame]
    Rx1_amp, cfar_threshold_Rx1, cfar_detection_Rx1, angles, Rx2_amp, cfar_threshold_Rx2, cfar_detection_Rx2, angles = detection_record.T
    
    # Calculate detected distances and angles for Rx1
    rx1_indexes_with_detections = np.where(cfar_detection_Rx1)[0]
    detected_distances_Rx1 = rx1_indexes_with_detections * radar_window.bin_size
    detected_angles_Rx1 = angles[rx1_indexes_with_detections]

    # Calculate detected distances and angles for Rx2
    rx2_indexes_with_detections = np.where(cfar_detection_Rx2)[0]
    detected_distances_Rx2 = rx2_indexes_with_detections * radar_window.bin_size
    detected_angles_Rx2 = angles[rx2_indexes_with_detections]
    
    # Call the plotting functions
    plot_polar_detections(ax_polar, detected_distances_Rx1, detected_angles_Rx1, detected_distances_Rx2, detected_angles_Rx2, 110)
    plot_cartesian_detections(ax_cartesian, Rx1_amp, Rx2_amp, cfar_detection_Rx1, cfar_detection_Rx2, cfar_threshold_Rx1, cfar_threshold_Rx2, detected_distances_Rx1, detected_distances_Rx2, radar_window.range_vector)
    
    detections = radar_window.get_most_recent_detections_split_xy()
    # detections = radar_window.get_most_recent_detections_combined_xy()
    plot_xy_detections(ax_xy, detections)
    
    
# Create animations for each figure separately
num_frames = 30
ani_polar = FuncAnimation(fig_polar, update, frames=range(num_frames), interval=250)
ani_cartesian = FuncAnimation(fig_cartesian, update, frames=range(num_frames), interval=250)
ani_xy = FuncAnimation(fix_xy, update, frames=range(num_frames), interval=250)

# # Display animations in Jupyter Notebook
from IPython.display import HTML
display(HTML(ani_xy.to_jshtml()))
display(HTML(ani_polar.to_jshtml()))
display(HTML(ani_cartesian.to_jshtml()))
